In [7]:
import tensorflow as tf

import numpy as np
import os
import time

In [8]:
path = '/content/bible.csv'

In [9]:
text = open(path, 'rb').read().decode(encoding="UTF-8")

print(f"Length of text: {len(text)}")

Length of text: 4191435


In [10]:
text

't\nIn the beginning God created the heaven and the earth.\n"And the earth was without form, and void; and darkness was upon the face of the deep. And the Spirit of God moved upon the face of the waters."\n"And God said, Let there be light: and there was light."\n"And God saw the light, that it was good: and God divided the light from the darkness."\n"And God called the light Day, and the darkness he called Night. And the evening and the morning were the first day."\n"And God said, Let there be a firmament in the midst of the waters, and let it divide the waters from the waters."\n"And God made the firmament, and divided the waters which were under the firmament from the waters which were above the firmament: and it was so."\nAnd God called the firmament Heaven. And the evening and the morning were the second day.\n"And God said, Let the waters under the heaven be gathered together unto one place, and let the dry land appear: and it was so."\nAnd God called the dry land Earth; and the 

In [11]:
print(text[:250])

t
In the beginning God created the heaven and the earth.
"And the earth was without form, and void; and darkness was upon the face of the deep. And the Spirit of God moved upon the face of the waters."
"And God said, Let there be light: and there was


Get unique texts

In [12]:
vocab = sorted(set(text))
print(f"{len(vocab)} unique characters")

66 unique characters


`tf.keras.layers.StringLookup` converts each character into a numeric id

In [13]:
ids_from_chars = tf.keras.layers.StringLookup(vocabulary=vocab, mask_token=None)

In [14]:
chars_from_ids = tf.keras.layers.StringLookup(vocabulary=ids_from_chars.get_vocabulary(), invert=True)

In [15]:
def text_from_ids(ids):
  return tf.strings.reduce_join(chars_from_ids(ids), axis=-1)

In [16]:
all_ids = ids_from_chars(tf.strings.unicode_split(text, input_encoding="UTF-8"))
all_ids

<tf.Tensor: shape=(4191435,), dtype=int64, numpy=array([60,  1, 22, ..., 54, 10,  1])>

In [17]:
ids_dataset = tf.data.Dataset.from_tensor_slices(all_ids)

In [18]:
for ids in ids_dataset.take(20):
  print(chars_from_ids(ids).numpy().decode('utf-8'))

t


I
n
 
t
h
e
 
b
e
g
i
n
n
i
n
g
 
G


In [19]:
seq_length = 100

In [20]:
sequences = ids_dataset.batch(seq_length+1, drop_remainder=True)

for seq in sequences.take(1):
  print(chars_from_ids(seq))

tf.Tensor(
[b't' b'\n' b'I' b'n' b' ' b't' b'h' b'e' b' ' b'b' b'e' b'g' b'i' b'n'
 b'n' b'i' b'n' b'g' b' ' b'G' b'o' b'd' b' ' b'c' b'r' b'e' b'a' b't'
 b'e' b'd' b' ' b't' b'h' b'e' b' ' b'h' b'e' b'a' b'v' b'e' b'n' b' '
 b'a' b'n' b'd' b' ' b't' b'h' b'e' b' ' b'e' b'a' b'r' b't' b'h' b'.'
 b'\n' b'"' b'A' b'n' b'd' b' ' b't' b'h' b'e' b' ' b'e' b'a' b'r' b't'
 b'h' b' ' b'w' b'a' b's' b' ' b'w' b'i' b't' b'h' b'o' b'u' b't' b' '
 b'f' b'o' b'r' b'm' b',' b' ' b'a' b'n' b'd' b' ' b'v' b'o' b'i' b'd'
 b';' b' ' b'a'], shape=(101,), dtype=string)


In [21]:
for seq in sequences.take(1):
  print(text_from_ids(seq).numpy())

b't\nIn the beginning God created the heaven and the earth.\n"And the earth was without form, and void; a'


A function to split input into two the input and target. the input is everything except the last and the target is everything except the first. the goal is for the model to take the input `Heave` and predict the next word which is in the target `eaven`

In [22]:
def split_input_target(sequence):
  input_text = sequence[:-1]
  target_text = sequence[1:]
  return input_text, target_text

In [23]:
split_input_target(list("Heaven"))

(['H', 'e', 'a', 'v', 'e'], ['e', 'a', 'v', 'e', 'n'])

In [24]:
dataset = sequences.map(split_input_target)

In [25]:
for input_example, target_example in dataset.take(1):
  print("Input: ", text_from_ids(input_example).numpy())
  print("Target: ", text_from_ids(target_example).numpy())

Input:  b't\nIn the beginning God created the heaven and the earth.\n"And the earth was without form, and void; '
Target:  b'\nIn the beginning God created the heaven and the earth.\n"And the earth was without form, and void; a'


## Create Training Batches

In [26]:
BATCH_SIZE = 64


BUFFER_SIZE = 10000

dataset = (
    dataset
    .shuffle(BUFFER_SIZE)
    .batch(BATCH_SIZE, drop_remainder=True)
    .prefetch(tf.data.AUTOTUNE)
)

dataset

<_PrefetchDataset element_spec=(TensorSpec(shape=(64, 100), dtype=tf.int64, name=None), TensorSpec(shape=(64, 100), dtype=tf.int64, name=None))>

In [27]:
len(dataset)

648

## Build the Model

In [28]:
# Length of the vocabulary in StringLookup Layer
vocab_size = len(ids_from_chars.get_vocabulary())

# The embedding dimension
embedding_dim = 256

# Number of RNN units
rnn_units = 1024

In [29]:
class MyModel(tf.keras.Model):
  def __init__(self, vocab_size, embedding_dim, rnn_units):
    super().__init__(self)
    self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
    self.gru = tf.keras.layers.GRU(rnn_units, return_sequences=True,
                                   return_state=True)
    self.dense = tf.keras.layers.Dense(vocab_size)


  def call(self, inputs, states=None, return_state=False, training=False):
    x = inputs
    x = self.embedding(x, training=training)
    if states is None:
      states = self.gru.get_initial_state(x)
    x, states = self.gru(x, initial_state=states, training=training)
    x = self.dense(x, training=training)

    if return_state:
      return x, states
    else:
      return x

In [30]:
model = MyModel(vocab_size=vocab_size,
                embedding_dim=embedding_dim,
                rnn_units=rnn_units)

## Try the model
To see if it behaves as expected
check the shape of the output

In [31]:
for input_example_batch, target_example_batch in dataset.take(1):
  example_batch_predictions = model(input_example_batch)
  print(example_batch_predictions.shape, "# (batch_size, sequence_length, vocab_size)")

(64, 100, 67) # (batch_size, sequence_length, vocab_size)


In [32]:
model.summary()

Model: "my_model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       multiple                  17152     
                                                                 
 gru (GRU)                   multiple                  3938304   
                                                                 
 dense (Dense)               multiple                  68675     
                                                                 
Total params: 4024131 (15.35 MB)
Trainable params: 4024131 (15.35 MB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [33]:
sampled_indices = tf.random.categorical(example_batch_predictions[0], num_samples=1)
sampled_indices = tf.squeeze(sampled_indices, axis=-1).numpy()

In [34]:
sampled_indices

array([13, 35, 38, 57, 50, 16,  0, 24,  5, 50, 36, 47, 59, 48, 16, 30, 55,
       51, 12, 44, 43, 29, 39, 38, 21,  8, 25,  8, 22, 26, 21, 47, 16, 15,
       35, 40, 31,  0, 30, 49, 39, 44, 56, 17, 13,  3, 21, 17, 62, 29, 56,
       61, 22,  7, 39, 29, 64, 49, 17, 62, 50, 51, 35, 39, 24, 59, 43, 13,
       56, 10,  3, 43, 62,  4, 14, 15, 34, 27, 37, 62, 21, 21,  1, 35, 50,
       66, 64, 25, 13, 47, 64,  1, 65, 47, 49,  0, 30, 51, 23, 40])

In [35]:
print("Input:\n", text_from_ids(input_example_batch[0]).numpy())
print()
print("Next Char Predictions:\n", text_from_ids(sampled_indices).numpy())

Input:
 b' be utterly destroyed."\n"Thou shalt neither vex a stranger, nor oppress him: for ye were strangers i'

Next Char Predictions:
 b'?VZqjC[UNK]K\'jWgshCQok;dcP[ZH,L,IMHgCBV]R[UNK]Qi[dpD?!HDvPpuI)[PxiDvjkV[Ksc?p.!cv"ABUNYvHH\nVjzxL?gx\nygi[UNK]QkJ]'


In [36]:
loss = tf.losses.SparseCategoricalCrossentropy(from_logits=True)

In [37]:
example_batch_mean_loss = loss(target_example_batch, example_batch_predictions)
print("Prediction shape: ", example_batch_predictions.shape, " # (batch_size, sequence_length, vocab_size)")
print("Mean loss:        ", example_batch_mean_loss)

Prediction shape:  (64, 100, 67)  # (batch_size, sequence_length, vocab_size)
Mean loss:         tf.Tensor(4.203879, shape=(), dtype=float32)


In [38]:
tf.exp(example_batch_mean_loss).numpy()

66.9455

In [39]:
model.compile(optimizer="adam", loss=loss)

In [41]:
checkpoint_dir = './training_checkpoints'

checkpoint_prefix = os.path.join(checkpoint_dir, "ckpt_{epoch}")

checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_prefix,
    save_weights_only=True
)

In [42]:
EPOCHS = 20

In [43]:
history = model.fit(dataset, epochs=EPOCHS, callbacks=[checkpoint_callback])

Epoch 1/20
648/648 [==============================] - 41s 55ms/step - loss: 1.7210
Epoch 2/20
648/648 [==============================] - 41s 60ms/step - loss: 1.1114
Epoch 3/20
648/648 [==============================] - 40s 57ms/step - loss: 1.0080
Epoch 4/20
648/648 [==============================] - 41s 60ms/step - loss: 0.9543
Epoch 5/20
648/648 [==============================] - 40s 59ms/step - loss: 0.9169
Epoch 6/20
648/648 [==============================] - 41s 60ms/step - loss: 0.8863
Epoch 7/20
648/648 [==============================] - 40s 57ms/step - loss: 0.8596
Epoch 8/20
648/648 [==============================] - 40s 58ms/step - loss: 0.8362
Epoch 9/20
648/648 [==============================] - 39s 58ms/step - loss: 0.8154
Epoch 10/20
648/648 [==============================] - 40s 60ms/step - loss: 0.7968
Epoch 11/20
648/648 [==============================] - 40s 58ms/step - loss: 0.7805
Epoch 12/20
648/648 [==============================] - 40s 59ms/step - loss: 0.7662
E

In [44]:
class OneStep(tf.keras.Model):
  def __init__(self, model, chars_from_ids, ids_form_chars, temperature=1.0):
    super().__init__()
    self.temperature = temperature
    self.model = model
    self.chars_from_ids = chars_from_ids
    self.ids_from_chars = ids_from_chars

    # Create a mask to prevent "[UNK]" from being generated
    skip_ids = self.ids_from_chars(['[UNK]'])[:, None]
    sparse_mask = tf.SparseTensor(
        # Put a -inf at each bad index.
        values=[-float('inf')]*len(skip_ids),
        indices=skip_ids,
        # Match the shape to the vocabulary
        dense_shape=[len(ids_from_chars.get_vocabulary())]
    )
    self.prediction_mask = tf.sparse.to_dense(sparse_mask)


  @tf.function
  def generate_one_step(self, inputs, states=None):
    # Convert strings to token IDs.
    input_chars = tf.strings.unicode_split(inputs, 'UTF-8')
    input_ids = self.ids_from_chars(input_chars).to_tensor()

    # Run the model.
    # predicted_logits.shape is [batch, char, next_char_logits]
    predicted_logits, states = self.model(inputs=input_ids, states=states, return_state=True)

    # Only use the last prediction
    predicted_logits = predicted_logits[:, -1, :]
    predicted_logits = predicted_logits/self.temperature
    # Apply the prediction mask: prevent "[UNK]" from being generated.
    predicted_logits = predicted_logits + self.prediction_mask

    # Sample the output logits to generate token IDs.
    predicted_ids = tf.random.categorical(predicted_logits, num_samples=1)
    predicted_ids = tf.squeeze(predicted_ids, axis=-1)

    # Convert from token ids to characters
    predicted_chars = self.chars_from_ids(predicted_ids)

    # Return the characters and model state.
    return predicted_chars, states

In [45]:
one_step_model = OneStep(model, chars_from_ids, ids_from_chars)

In [55]:
start = time.time()
states = None
next_char = tf.constant(["Rapture"])
result = [next_char]

for n in range(1000):
  next_char, states = one_step_model.generate_one_step(next_char, states=states)
  result.append(next_char)

result = tf.strings.join(result)
end = time.time()
print(result[0].numpy().decode('utf-8'))
print('\nRun time:', end - start)

Rapture the son of Saul with him, and chose not her; and nothing walk of gold in the midst of them for his neighbour;"
"Concerning peace, because their trespass is toward the east gate of the house,"
"Said to God, I am a divine service gate; for in the daynis is in thine heart that thou hast not rich: but his years know not thereon."
"But if any rejecting no lot far off, let him give an again many day, nor betaining of the prophets which are by faith."
"Howbeit this canserward shall more to whom the LORD thy God left me: therefore I also am, there may be darkness.
"Yea, thou cleansed, and will give thee mercy, and give glory of God: but I in it?"
"When they said one to another, What made no corruption, God seek him as many as are opened and evil;"
"Where I am no bread with righteousness; and every one that will be destroyed from well pleasure."
"And when they have cast both, and now accomplish it without children, and tempested from before thee: for that ye have been faithful and just 

### Export the generator

In [56]:
tf.saved_model.save(one_step_model, 'one_step')
one_step_reloaded = tf.saved_model.load('one_step')

In [61]:
states = None
next_char = tf.constant(['In the Beginning'])
result = [next_char]

for n in range(100):
  next_char, states = one_step_reloaded.generate_one_step(next_char, states=states)
  result.append(next_char)


print(tf.strings.join(result)[0].numpy().decode('utf-8'))

In the Beginning Is accept as an hin of principal sing for me."
"I will shew him also that I should reign over him: 
